# Part 2: Pandas and GeoPandas

Pandas is based on numpy, therefore it provides vectorized computation as well. 

&rarr; [Pandas User Guide: Accelerated Operations](https://pandas.pydata.org/pandas-docs/stable/user_guide/basics.html#accelerated-operations)

## 1. Brief Introduction to Pandas and GeoPandas

In [1]:
import pandas as pd

In [2]:
file_path = "./data/new_york_hotels.csv"

In [8]:
hotels = pd.read_csv(file_path, encoding='cp1252')

In [9]:
hotels.head()

ean_hotel_id                                     name   
0        269955       Hilton Garden Inn Albany/SUNY Area  \
1        113431     Courtyard by Marriott Albany Thruway   
2        108151                    Radisson Hotel Albany   
3        254756  Hilton Garden Inn Albany Medical Center   
4        198232  CrestHill Suites SUNY University Albany   

                 address1    city state_province postal_code  latitude   
0     1389 Washington Ave  Albany             NY       12206  42.68751  \
1  1455 Washington Avenue  Albany             NY       12206  42.68971   
2             205 Wolf Rd  Albany             NY       12205  42.72410   
3     62 New Scotland Ave  Albany             NY       12208  42.65157   
4  1415 Washington Avenue  Albany             NY       12206  42.68873   

   longitude  star_rating  high_rate  low_rate  
0  -73.81643          3.0   154.0272  124.0216  
1  -73.82021          3.0   179.0100  134.0000  
2  -73.79822          3.0   134.1700   84.1600  
3  -73.77638          3.0   308.2807  228.4597  
4  -73.81854          3.0   169.3900   89.3900

**E:** Calculate the mean star_rating. 

**E:** How many unique cities are in the `city` column?

**E:** How many hotels are there in Newark?

**E:** How many hotels are there in each city?

**E:** How many hotels have the name 'Hilton' hotels are there?

**E:** Calculate the average star rating and its standard deviation per city.

## 2. How to use vectorized computation in Pandas and Geopandas

To perform geospatial operations with the data, we need to create a `geometry` column which contains Point geometries based on the `latitude` and `longitude` columns for each hotel. This can be done in different ways. 

**Exercise 2.1:** Implement this in different ways and measure the execution time.  

##### Using the `iterrows()` and a for loop

##### Using list comprehension

##### Using the `apply()` method

##### Using geopandas built-in function

### Geospatial Operations in GeoPandas 

Yesterday we saw that OGR is faster than shapely. Still, geopandas uses shapely. Let's see how they compare when using vectorization. 

instead of only polygon, we will create a list of n polygons. For each one, we will generate random coordinates. 

In [35]:
# Create 1000 random polygons using shapely 
import random   
import shapely.geometry as sg

n = 100000
random_coordinates = [[(random.uniform(0, 10), random.uniform(0, 10)) for i in range(5)] for j in range(n)]


#### OGR 

Create a list of OGR polygons and calculate the area of each polygon.

In [21]:
from osgeo import ogr

In [22]:
def create_polygon(coords):          
    ring = ogr.Geometry(ogr.wkbLinearRing)
    for coord in coords:
        ring.AddPoint(coord[0], coord[1])

    # Create polygon
    poly = ogr.Geometry(ogr.wkbPolygon)
    poly.AddGeometry(ring)
    return poly

In [23]:
# Create 1000 random polygons using shapely 
import random   

random_ogr_polygons = []
for i in range(n):
    start_point = (random.uniform(0, 10), random.uniform(0, 10))
    coordinates = [start_point] + [(random.uniform(0, 10), random.uniform(0, 10)) for i in range(3)] + [start_point]
    new_polygon = create_polygon(coordinates)
    random_ogr_polygons.append(new_polygon)

In [24]:
import numpy as np

In [27]:
%%timeit
areas = np.empty(n)
for i, poly in enumerate(random_ogr_polygons):
    areas[i] = poly.GetArea()

32.4 ms ± 832 μs per loop (mean ± std. dev. of 7 runs, 10 loops each)


#### 1. Implementation in pure shapely

In [28]:
random_shapely_polygons = [sg.Polygon(j) for j in random_coordinates]  

In [ ]:
import numpy as np
import shapely

Calculate the area of each polygon

In [29]:
%%timeit


369 ms ± 947 μs per loop (mean ± std. dev. of 7 runs, 1 loop each)


### 2. Implementation in GeoPandas

Calculate the area of each polygon using GeoPandas.

In [30]:
import geopandas as gpd

In [31]:
%%timeit


1.49 ms ± 13.1 μs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


It uses shapely but somehow the calculation is now faster than OGR. What Geopandas does in the background is ...

1. Create a vectorized representation of the geometries

2. Use a vectorized function to calculate the area

In [33]:
%%timeit

1.33 ms ± 24.2 μs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


This is a very new feature only available for shapely version > 2.0.0. Previously, geopandas used the pygeos package to implement vectorized geometric operations. In the latest shapely version 2.0.0, pygeos was integrated into shapely, so now shapely also supports vectorized computations. Be careful when using a versions < 2.0, they might be slower . 

### Resources

#### More on Pandas and vectorization
Watch this talk by __Sofia Heisler's repository [PyCon 2017: Optimizing Pandas Code for Performance](https://github.com/s-heisler/pycon2017-optimizing-pandas)__ to get a more indepth look into vecotrized computation using pandas. 

&rarr; Watch her talk on [YouTube](https://www.youtube.com/watch?v=HN5d490_KKk) I really recommend it (especially if you like panda GIFs)

&rarr; Read her [blog post](https://engineering.upside.com/a-beginners-guide-to-optimizing-pandas-code-for-speed-c09ef2c6a4d6)

[Introducing pygeos](https://caspervdw.github.io/Introducing-Pygeos/)

[PyGEOS Documentation](https://pygeos.readthedocs.io/en/latest/)
   

[Cythonize Pandas](https://pandas.pydata.org/pandas-docs/stable/user_guide/enhancingperf.html)

https://stackoverflow.com/questions/52673285/performance-of-pandas-apply-vs-np-vectorize-to-create-new-column-from-existing-c

https://www.google.com/url?q=http://homepages.math.uic.edu/~jan/mcs275/running_cython.pdf&sa=U&ved=2ahUKEwiq_M3-vfrqAhWF-KQKHXBXCfwQFjAAegQICRAB&usg=AOvVaw0jX9BZrTt2aPsxKo30zmDb
